In [1]:
import pandas as pd
import seaborn as sns
import time
import re
import nltk
import math
import os
from Bio.SeqUtils.ProtParam import ProteinAnalysis
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
def fasta_parser(filename):
    if os.path.exists(filename):
        pass
    else:                     
        print("The file, %s, does not exist" % filename)
        
    file = open(filename,mode='r')
    rec_all = file.read()
    file.close()
    # remove all whitespace from string all_of_it
    rec_all = rec_all.replace(' ','')
    # split records by > 
    records = rec_all.split('>')
    # Parse out the headers & sequences for each record
    headers = []
    sequences = []
    for rec in records:
        s = ''
        data = rec.split('\n')
        sq = s.join(data[1:])
        if len(data[0]) > 0:
            headers.append(data[0])
   
        if (len(sq) > 0):
            sequences.append(s.join(data[1:]))
    
    return headers, sequences

In [3]:
# concatenate all relevant fasta files into one fasta file use glob
# see https://stackoverflow.com/questions/17749058/combine-multiple-text-files-into-one-text-file-using-python/17749339
# Note the code below works with no bizzare artifacts from globbing or concatenation
#read_files = glob.glob("*.fasta")

#with open("isomerase_2000.fasta", "wb") as outfile:
    #for f in read_files:
        #with open(f, "rb") as infile:
            #outfile.write(infile.read())

In [4]:
f_name = 'uniprot-ironSulfur-unreviewed.fasta'
t_head, t_seqs = fasta_parser(f_name)

In [5]:
for hd in t_head[0:5]:
    print(hd)
    print()

tr|T0M7Z9|T0M7Z9_CAMFRMultifunctionalfusionproteinOS=CamelusferusOX=419612GN=CB1_001086024PE=3SV=1

tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMIMultifunctionalfusionproteinOS=SymbiodiniummicroadriaticumOX=2951GN=SAHHPE=3SV=1

tr|A0A2P6TTG2|A0A2P6TTG2_CHLSOSuccinatedehydrogenase[ubiquinone]iron-sulfursubunit,mitochondrialOS=ChlorellasorokinianaOX=3076GN=C2E21_4328PE=3SV=1

tr|A0A091CKG8|A0A091CKG8_FUKDAMultifunctionalfusionproteinOS=FukomysdamarensisOX=885580GN=H920_19443PE=3SV=1

tr|Q59QN7|Q59QN7_CANALSuccinatedehydrogenase[ubiquinone]iron-sulfursubunit,mitochondrialOS=Candidaalbicans(strainSC5314/ATCCMYA-2876)OX=237561GN=SDH2PE=3SV=1



In [6]:
for sq in t_seqs[0:5]:
    print(sq)
    print()

...



In [7]:
print(len(t_seqs))

39599


In [8]:
t_seqs2 = list(set(t_seqs))
print(len(t_seqs2))

31203


In [9]:
from Bio import SeqIO
records = list(SeqIO.parse(f_name, "fasta"))


In [10]:
seq_ids =[]
seqs = []
#for record in SeqIO.parse("isomerase_2000.fasta", "fasta"):
for record in SeqIO.parse(f_name, "fasta"):
    print(repr(record.seq))
    print()
    seq_ids.append(record.id)
    seqs.append(str(record.seq))

Seq('MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCKGPGDACRR...GGC', SingleLetterAlphabet())

Seq('MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPFLQNYTIDL...YRY', SingleLetterAlphabet())

Seq('MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFLVYRWNPDS...AIG', SingleLetterAlphabet())

Seq('MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYRWDPDKTGD...AVR', SingleLetterAlphabet())

Seq('MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQPKMQTYEV...AFD', SingleLetterAlphabet())

Seq('MNLLRRQPRLLNKRSTWLFRNYVLANRDVSEPVSRPAAPMSTLSIPGPALAAAT...GKA', SingleLetterAlphabet())

Seq('MASVVNEGGRGRRRVGSSSTSKIGIVNQKTKTNGPSPPRAPRPPKKRGEKETPP...ASW', SingleLetterAlphabet())

Seq('VRGFQQKAGDIYPDRDAAEHLECVWMQGNAAEQRPHYGPKILHGFFAHIRAFSR...TAS', SingleLetterAlphabet())

Seq('MAQFTLPTNSKVTSGNHYPAPEGATNTKTFEIYRWSPDDDANPRLDSFEIDLDD...RQG', SingleLetterAlphabet())

Seq('MAAAALLRRSQTAARALLSPAPLSSRLVASKPHSSSPAPPPPSASTKTFSIYRW...ASW', SingleLetterAlphabet())

Seq('MAAALLRRSPAVRALLSPALSSRLVASKPHSSSPAPPPPAKAASSTKTFSIYRW...PSA', Si

Seq('MSDNERTIVVRVLKFDPQSAVSKPHFKEYQLKETPSMTLFIVLNLIREHQDPDL...KSR', SingleLetterAlphabet())

Seq('MSDNERTIVVRVLKFDPQSAVSKPHFKEYQLKETPSMTLFIALNLIREHQDPDL...KSR', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCESLKGILEQVKRVQITLHGSLA...LKC', SingleLetterAlphabet())

Seq('MALSVFDLFSIGIGPSSSHTVGPMRAAVLFVERLRDEGRLDQVARVRSELFGSL...IEC', SingleLetterAlphabet())

Seq('MDMISAFDIFKIGIGPSSSHTVGPMNAGKSFIDRLESSGLLTATSHIVVDLYGS...VCG', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCESLKGVLEQVVRVQITLHGSLA...LEC', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGSMEAGARFCGLLKGILEQVKRVQITLHGSLA...LEC', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCESLKGVLEQVVRVQITLHGSLA...LEC', SingleLetterAlphabet())

Seq('MSDNERTIVVRVLKFDPQSAVSKPHFKEYQLKETPSMTLFIALNLIREHQDPDL...KSR', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCGLLKGILEQVERVQITLHGSLA...LKC', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCESLKGVLEQVMRVQITLHGSLA...LKC', Si


Seq('MAISVFDLFSIGIGPSSSHTVGPMRAARMFARRLRNEDVLSSVAAVRSELYGSL...IEC', SingleLetterAlphabet())

Seq('MSQVTYKVRRFDGEKAYIQEYQFEHQPGKTILWGLIKIKEELDPTLTFTAACRS...SEK', SingleLetterAlphabet())

Seq('MAISVFDLFKIGIGPSSSHTVGPMRAAALFVQHLRERGMLEQVRRVEVQLYGSL...VEC', SingleLetterAlphabet())

Seq('MTDPRPRQRSRIDASAAISVVDLFTVGVGPSSSHTVGPMRAARMFMESLAACPE...VAC', SingleLetterAlphabet())

Seq('MDMSVFDLFKIGIGPSSSHTVGPMVAARRFLLECGPLDSAVGVEAHLYGSLALT...AAC', SingleLetterAlphabet())

Seq('MSSNLSIFKVGVGPSSSHTLGPMLAGNMFCEKIKDKITQITKIQIRLYGSLSLT...SVC', SingleLetterAlphabet())

Seq('MMAISVFDMFKIGIGPSSSHTVGPMRAGALFVTELRNQDRLHSVERIEVRLYGS...IEC', SingleLetterAlphabet())

Seq('MISIFDLFSVGIGPSSSHTVGPMRAARTFVTGLKADGLLTETVRIRAELFGSLG...IEC', SingleLetterAlphabet())

Seq('MAQLETAAGMLHVKVWRGGQHGVFQDYELPRRDNQTVLDVATHIQRHLDPTLSY...ATP', SingleLetterAlphabet())

Seq('MAVSVFDLFSIGIGPSSSHTVGPMRAARMFAGRLKNEGVLAHTASVRAELYGSL...IEC', SingleLetterAlphabet())

Seq('MSDNERTIVIRVLKFDPQSAVSKPHFKEYQLKETPSMTLFIALNLIREHQDPDL...KSR', S

Seq('MTHSTTRRTFIVQTLGLCAALAAARTSVAAPPLVDENDATAKSLGYRAHASAVD...KRA', SingleLetterAlphabet())

Seq('MSTALVDPDAVANLEEADDTGIQAFLVTFIVRRFNPEVDEEPRWVDYDVEVYST...GKP', SingleLetterAlphabet())

Seq('MAELRLPPNSVVEKGREHKENEEMLRPRKIKIYRYNPDLDENPTIDSFEIDLSK...RGM', SingleLetterAlphabet())

Seq('MISVFDMFSIGIGPSSSHTVGPMKAAKLFVEQLKNEHKLTQTTRVKCELFGSLG...TEC', SingleLetterAlphabet())

Seq('MLSVLDMFKIGIGPSSSHTVGPMRITRRALIEAKTAGVLEQAARVRVELQGSLA...VEC', SingleLetterAlphabet())

Seq('MGAQSVAFSADLPPLSPNDPMAAALGYVEDATTTDVAKFSRYKTGQECANCQLY...KAS', SingleLetterAlphabet())

Seq('MKLEFSIYRYNPDVDDAPHMQDYTLEAEEGRDMMLLDALIQLKEKDPSLSFRRS...RSA', SingleLetterAlphabet())

Seq('MTISVFDLFKVGIGPSSSHTVGPMKAAYLFVDGLRDDGQLDEVTKVHVELFGSL...VEC', SingleLetterAlphabet())

Seq('MSANRIQLVEILRYDPAKDAEPYLEKFEVPFNETMSVLDALGYIKDHLDKDLSY...MEA', SingleLetterAlphabet())

Seq('MTHSTTRRTFIVQTLGLCAALAAARTAVAAPPLVDENDATAKSLGYRAHASAVD...KRA', SingleLetterAlphabet())

Seq('MVEFNLPANSVVKEGKTFSAPADAKNVRSFKIYRFDPDSGDNPRTDTYDIDLDK...RRA', Si

Seq('MERTITVRLARYSPERPEEGQSFATYEVPMRPKWMVLDALNYIKNELDPTVTFR...RRP', SingleLetterAlphabet())

Seq('MATFTLPANSKIKSNGKVHKSTGKRVKSFKVYRYDPDSGENPRYDKFEIDLDEC...RAI', SingleLetterAlphabet())

Seq('MSSTRRIFLARTAGLCAGLTFYRELLASQAHLAENDPAAQALGYKADAATVDRA...KRT', SingleLetterAlphabet())

Seq('MSISVFDLFKIGIGPSSSHTVGPMRAAYDFVQELRRQDLLERVARVEVHLHGSL...IEC', SingleLetterAlphabet())

Seq('MADFFLPKNSKVQKGRVHASSTAGKVKKFKVYRYDPDSGENPRYDTFEVDTDNC...RHI', SingleLetterAlphabet())

Seq('MYSETTAVPVDKPKIVELRVLRYRPASDTEPVFMTYHLPFTDDMSVLQALQAVK...PSA', SingleLetterAlphabet())

Seq('MAISVFDLFSVGIGPSSSHTVGPMRAAARFAARLRAEGLLSGVAHVRAELFGSL...IEC', SingleLetterAlphabet())

Seq('MQLTFSVYRYNPEVDNAPRMQDYTLDVEEGQDMMVLDALILLKEQDPTLSFRRS...RAV', SingleLetterAlphabet())

Seq('MFLSVFDMFKVGVGPSSSHTIGPMVAAARFLEHLRAQPFAVAGLRASLHGSLAF...PNC', SingleLetterAlphabet())

Seq('MISVFDIFKIGIGPSSSHTVGPMKAGKQFTDDLIARNLLKDVTRVVVDVYGSLS...ACD', SingleLetterAlphabet())

Seq('MFLSVFDLFKIGIGPSSSHTMGPMTAARRFLDEVAGDDWPRPAGAKIARIGASL...VEC', Si

...

Seq('MVQLTLPKNSKVTDGKTWAYPSGADHVREYRIYRWNPDDGKNPRMDTYYVDCDD...RQM', SingleLetterAlphabet())

Seq('MTKFHIFRFDPKADAAPRFQDYEVPEAKGMTVLDGLIHILEELDPSLAYRSSCR...AKA', SingleLetterAlphabet())

Seq('MESCLDIFKIVIGPSSSRTVGPMRAACHFISLLREQETLPLIREIEIELYGALS...KRG', SingleLetterAlphabet())

Seq('MVELTLPKNSKVQQGKTWPKPEGATNLREYRIYRWSPDDDENPRMDTYFVDMDD...RRV', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTVGPMNAGKCFIDRLIDSGDLPRTTRITVDLYGSLS...VCG', SingleLetterAlphabet())

Seq('MEVYFKILRQRPNDTPYLENFTLEVEAGNTILDCLNRIKWELDGTLAFRKNCRN...SRS', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTVGPMNAGKCFIDRLIDSGDLPRTTRITVDLYGSLS...VCG', SingleLetterAlphabet())

Seq('MCDYNGLSISGLMMHNELALRSKAEIDAGFARIWQVMHDGIERGMNTEGVLPGP...TGY', SingleLetterAlphabet())

Seq('MISVFDIFKIGIGPSSSHTVGPMKAGKQFTDDLIARGILTDVTRVVVDVYGSLS...TCD', SingleLetterAlphabet())

Seq('MSNVRSQLTVSLWRGGEDGRYQSYQVPLRENQTVLDVVTWVQRNLEPSLAYRFA...IEA', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTVGPMNAGKCFIDRLIDSGDLPRTTRITVDLYGSLS...VCG', Si

Seq('MESCLDIFKIVIGPSSSRTVGPMRAACHFISLLREQETLPLIREIEIELYGALS...KRG', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTIGPMNAGKCFIDRLNDSGDLPRTTRITVDLYGSLS...VCG', SingleLetterAlphabet())

Seq('MSNLSIFKIGVGPSSSHTLGPMLAGNLFCKKVAKKLDEIDRVEVTLYGSLSLTG...TVC', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTVGPMNAGKCFIDRLIDSGDLPRTTRITVDLYGSLS...VCG', SingleLetterAlphabet())

Seq('MAEMKNLKIEVVRYNPEVDTAPHSAFYEVPYDATTSLLDALGYIKDNLAPDLSY...KPR', SingleLetterAlphabet())

Seq('MISAFDIFKIGIGPSSSHTVGPMNAGKCFIDRLIDSGDLPRTTRITVDLYGSLS...VCG', SingleLetterAlphabet())

Seq('MAEMKNLKVEVVRYNPETDTAPHSAFYEVPYDETTSLLDALGYIKDNLSPDLSY...KPR', SingleLetterAlphabet())

Seq('MAEMKNLKVEVVRYNPETDTAPHSAFYEVPYDETTSLLDALGYIKDNLSPDLSY...KPR', SingleLetterAlphabet())

Seq('MESCLDIFKIVIGPSSSRTVGPMRAACHFISLLREQETLPLIREIEIELYGALS...KRG', SingleLetterAlphabet())

Seq('MESCLDIFKIVIGPSSSRTVGPMRAACHFISLLREQETLPLIREIEIELYGALS...KRG', SingleLetterAlphabet())

Seq('MISLFDMFKVGIGPSSSHTVGPMKAGKQFVDDLVEKGLLNAVTRVAVDVYGSLS...QCD', Si


Seq('MAALRHSTRILGTARTASIRPSVAFSRSMATVSEVEEQKPRMKTFQIYRWNPDT...LGA', SingleLetterAlphabet())

Seq('MNTTFLSRPLLRATLISARPTTGLRTLASVATPQTAPTEPGSKKPNTKQFQIYR...FGS', SingleLetterAlphabet())

Seq('MASLRSSARLVAASRSAFRPATAIRSFASVAPAATSPATAPSSEPAPAAPRTKT...LAF', SingleLetterAlphabet())

Seq('MLRNQIATIRSLRLFDRTCRCGATMAAPAKMKHMKTFEIYRFNPEQPGSKPRMQ...ADF', SingleLetterAlphabet())

Seq('MKLQFSIYRYNPDMDNAPRMQDYTLEVPEGRDMMLLDALIQIKEQDPTLSFRRS...HSA', SingleLetterAlphabet())

Seq('MKLEFSIYRYNPDVDNAPRMQDYTLEGEEGRDMMLLDALIQLKEKDPSLSFRRS...RSA', SingleLetterAlphabet())

Seq('MAEFTLPKNSKIKSGKIFSEANGATRKKKFHIYRWEPDSGKNPRLDVYELNLDN...RIS', SingleLetterAlphabet())

Seq('MRLEFSIYRYNPDVDDAPRMQDYTLEAEEGRDMMLLDALIQLKEKDPSLSFRRS...RNA', SingleLetterAlphabet())

Seq('MISLFDMFKVGIGPSSSHTVGPMKAGKQFVDDLVEKGLLDNVTRVAVDVYGSLS...QCD', SingleLetterAlphabet())

Seq('MISIFDIFKIGIGPSSSHTVGPMKAAAAFADLLHAENLDTQVARIVIEVYGSLA...VEC', SingleLetterAlphabet())

Seq('MISVFDIYKIGVGPSSSHTVGPMKAGKEFIDDLRAMGKLRDITKITVDVYGSLS...VIC', S


Seq('MSLSVFDLFKIGIGPSSSHTVGPMRAAARFAEGLRREGLLTATTCVKVELYGSL...IEC', SingleLetterAlphabet())

Seq('MKKECISVFDIFKIGVGPSSSHTLGPWRAALRFLETVKQKGIEKVTSARVLLYG...PEC', SingleLetterAlphabet())

Seq('MISAFDMFSIGIGPSSSHTVGPMRASRLFVNDLQEQQLLANVTDIKVELYGSLG...IEC', SingleLetterAlphabet())

Seq('MASFSILSIFKIGVGPSSSHTIGPMEAGARFCGLLKGVLDQVMRVQITLHGSLA...LKC', SingleLetterAlphabet())

Seq('MFLSVFDVFKIGVGPSSSHTMGPMSAANRFLDLILSDEWPRPSSGAQVAAIKVS...VEC', SingleLetterAlphabet())

Seq('MAVSVFDLFKIGIGPSSSHTVGPMRAAARFAEHWLEEKGVLDRVVRVHAELYGS...IEC', SingleLetterAlphabet())

Seq('MAISVFDLFKVGIGPSSSHTVGPMRAAATFAQALTDQHLLSQTRRVEVRLYGSL...VEC', SingleLetterAlphabet())

Seq('MGSVFDIFKIGIGPSSSHTVGPMRAGKLFIDQLIEKNLMSSVTTITADVYGSLS...RCE', SingleLetterAlphabet())

Seq('MLSIFDIYKIGVGPSSSHTNGPMIAGYHFTRLIESNLAKVVRIQVDLYGSLSLT...PCE', SingleLetterAlphabet())

Seq('MRLEFSIYRYNPEVDDKPRMQDYSLEAEDGRDMMLLDALIRLKEKDPTLAFRRS...RGA', SingleLetterAlphabet())

Seq('MQLTFSIYRYNPDVDDAPRMQDYQLEVEEGQDMMVLDALIALKEKDPSLSFRRS...RAV', S


Seq('RFAPIAFRRGMATTIEHTKEPISATAEALSASRPPIKETKTSTVKEPQMDADAK...FAG', SingleLetterAlphabet())

Seq('LHEDEDVLGIHAPDVHQYSYAESAKSILYTALAFAAFGYVASGLVPERNVAPRD...ATA', SingleLetterAlphabet())

Seq('MAALRSSSRLVGAFSRTAAFRPGAVFTRSMASVSEPPKDSDANLKSFQIYRWNP...FGN', SingleLetterAlphabet())

Seq('RQTALRPAVFSRGFASVTDTVARDPISKVAESIVPDPSRKIVPESKTSTKQEPE...ALA', SingleLetterAlphabet())

Seq('MAALRSSSRVFGSATQAAFRPAVTISRRGLATPSDRVPATKEPKMKKFTVYRWN...MAF', SingleLetterAlphabet())

Seq('MASIRAFTRLATQRTAVRPAVFSRGFASVNDVHARDPISKTAEKIAPDASRSPI...AFT', SingleLetterAlphabet())

Seq('MAALRSSSRLVGAFSRTAAFRPGAVFTRSMASVSEPPKDSDANLKTFQIYRWNP...FGN', SingleLetterAlphabet())

Seq('MAALRSATRFVAPSRSVLRSSFAGRSYATVTEKSTYDTSASRPPIPASKTTTVE...MAF', SingleLetterAlphabet())

Seq('MALRLATRRFAPIAFRRGMATTIEHTKEPISATAEALSASRPPIKETKTSTVKE...FTG', SingleLetterAlphabet())

Seq('MSGIGLRSVNNLKKCFSIRGFSTAAPSRMAQEAPASKQNTKKFMIYRWNPETPA...ASD', SingleLetterAlphabet())

Seq('MAALRSSSRLVGAFSRTAALRPGAVFTRSMASVSEPPKDSNANLKSFQIYRWNP...FGN', S

In [11]:
print(len(seq_ids))
print()
print(len(seqs))

39599

39599


In [12]:
seqs[0:3]

['...']

In [13]:
seqID = []
for item in records:
    seqID.append(item.id)
    print(item.id)
    print()

tr|T0M7Z9|T0M7Z9_CAMFR

tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI

tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO

tr|A0A091CKG8|A0A091CKG8_FUKDA

tr|Q59QN7|Q59QN7_CANAL

tr|Q9VWN3|Q9VWN3_DROME

tr|K3YHV8|K3YHV8_SETIT

tr|A0A1Q9C7M6|A0A1Q9C7M6_SYMMI

tr|A0A2E4ASZ9|A0A2E4ASZ9_9PROT

tr|I1I0K5|I1I0K5_BRADI

tr|K7U1I2|K7U1I2_MAIZE

tr|A0A1D6LEN4|A0A1D6LEN4_MAIZE

tr|A0A0V1PMK3|A0A0V1PMK3_9BILA

tr|A0A0V0UWP4|A0A0V0UWP4_9BILA

tr|A0A0V0X3M6|A0A0V0X3M6_9BILA

tr|A0A0V1A8M9|A0A0V1A8M9_9BILA

tr|A9V595|A9V595_MONBE

tr|Q8SXL9|Q8SXL9_DROME

tr|A0A1Z5R7Q4|A0A1Z5R7Q4_SORBI

tr|H2PY56|H2PY56_PANTR

tr|M0Y6W8|M0Y6W8_HORVV

tr|G6A0R6|G6A0R6_9PROT

tr|A0A0B0HDH8|A0A0B0HDH8_SOVGS

tr|G5ZWL8|G5ZWL8_9PROT

tr|H9GN10|H9GN10_ANOCA

tr|A0A2H3YDX2|A0A2H3YDX2_PHODC

tr|A0A1H3CVL0|A0A1H3CVL0_ALLWA

tr|A0A3R8RSI7|A0A3R8RSI7_9MICO

tr|A0A104JAU2|A0A104JAU2_9BURK

tr|A0A0B9H2K2|A0A0B9H2K2_9GAMM

tr|A0A2J6I6W1|A0A2J6I6W1_9BACT

tr|J0QCX1|J0QCX1_9RHIZ

tr|A0A118S034|A0A118S034_9BURK

tr|M3K9J8|M3K9J8_HELPX

tr|A0A3R9P9Q5|A0A3R9P9Q5_9BACI




tr|A0A2N8KE42|A0A2N8KE42_9BURK

tr|A0A4R4MCY1|A0A4R4MCY1_9ACTN

tr|A0A1F4D0C3|A0A1F4D0C3_9PROT

tr|A0A1N6YU42|A0A1N6YU42_9BURK

tr|A0A344LXI9|A0A344LXI9_9FLAO

tr|A0A560MP63|A0A560MP63_9MICO

tr|A0A1V3NZ63|A0A1V3NZ63_9GAMM

tr|A0A420DJQ4|A0A420DJQ4_9RHOB

tr|A0A0T0MA21|A0A0T0MA21_9FLAO

tr|V0VFI4|V0VFI4_ECOLX

tr|A0A0Q5HBF4|A0A0Q5HBF4_9RHIZ

tr|A0A1F8VVI1|A0A1F8VVI1_9BURK

tr|A0A3G8M2K5|A0A3G8M2K5_9RHIZ

tr|A0A1V3P810|A0A1V3P810_9GAMM

tr|U4R8F9|U4R8F9_HELPX

tr|U6RIR7|U6RIR7_9BACE

tr|H4UHZ1|H4UHZ1_ECOLX

tr|A0A4R1IH99|A0A4R1IH99_9BURK

tr|X5UUK4|X5UUK4_9RHIZ

tr|A0A553AFT9|A0A553AFT9_9FLAO

tr|A0A1L7AAN2|A0A1L7AAN2_9PROT

tr|J7LNA9|J7LNA9_9MICC

tr|H4UPG4|H4UPG4_ECOLX

tr|A0A2U2ZZC2|A0A2U2ZZC2_9ACTN

tr|A0A514WHD1|A0A514WHD1_9SPHN

tr|A0A2A9ENW1|A0A2A9ENW1_9MICO

tr|A0A2E6HAT5|A0A2E6HAT5_9PROT

tr|A0A2H0J2S5|A0A2H0J2S5_9BURK

tr|A0A420DU26|A0A420DU26_9RHOB

tr|A0A147IPN3|A0A147IPN3_9SPHN

tr|A0A1C0B896|A0A1C0B896_9PROT

tr|J7LKI9|J7LKI9_9MICC

tr|A0A0H2WG40|A0A0H2WG40_BURMA

tr|A0A4


tr|A0A100WR76|A0A100WR76_MYCFO

tr|A0A2M9E9Z0|A0A2M9E9Z0_9GAMM

tr|A0A0L0Q8T6|A0A0L0Q8T6_HELPX

tr|A0A3M3WQK4|A0A3M3WQK4_PSEMA

tr|A0A0D7CGC5|A0A0D7CGC5_9ACTN

tr|H4INI3|H4INI3_ECOLX

tr|A0A252AS69|A0A252AS69_9PROT

tr|A0A5B9I7H6|A0A5B9I7H6_HELPX

tr|A0A1V3ARY9|A0A1V3ARY9_HELPX

tr|A0A2S9SAM7|A0A2S9SAM7_HAEIF

tr|A0A4R2FPN7|A0A4R2FPN7_9VIBR

tr|A0A4R2ZVV8|A0A4R2ZVV8_9SPHI

tr|A0A0P7VRU4|A0A0P7VRU4_9RHOB

tr|A0A1I6W634|A0A1I6W634_9ACTN

tr|A0A4R2G1R3|A0A4R2G1R3_9VIBR

tr|A0A432Y950|A0A432Y950_9GAMM

tr|A0A521BGT3|A0A521BGT3_9RHOB

tr|A0A519JFU0|A0A519JFU0_9GAMM

tr|Q47Y35|Q47Y35_COLP3

tr|H4IXE0|H4IXE0_ECOLX

tr|A0A2T7K1F2|A0A2T7K1F2_9ACTN

tr|A0A2T6VKN7|A0A2T6VKN7_HELPX

tr|A0A1Q4DGU0|A0A1Q4DGU0_9GAMM

tr|A0A148KMS6|A0A148KMS6_9ALTE

tr|E3PE24|E3PE24_ECOH1

tr|A0A384G9Y3|A0A384G9Y3_9RHOB

tr|A0A4P6KLK5|A0A4P6KLK5_BRUML

tr|A0A391PFV4|A0A391PFV4_9MYCO

tr|A0A4P6KL47|A0A4P6KL47_BRUML

tr|A0A0L8C677|A0A0L8C677_ENSAD

tr|A0A4S2TXY1|A0A4S2TXY1_ENSAD

tr|A0A3P5VUD4|A0A3P5VUD4_9SPIR

tr|A0A2

tr|C6RIF4|C6RIF4_9PROT

tr|A0A2N6FMF6|A0A2N6FMF6_9PROT

tr|A0A1Y2L685|A0A1Y2L685_9PROT

tr|A0A2D5JDD8|A0A2D5JDD8_9PROT

tr|A0A4Q1TVW7|A0A4Q1TVW7_9BRAD

tr|A0A1Q3UGJ7|A0A1Q3UGJ7_9SPHI

tr|D0IFB1|D0IFB1_9VIBR

tr|A0A3S3TL86|A0A3S3TL86_9SPHN

tr|A0A0L6CUB3|A0A0L6CUB3_9RHOB

tr|A0A2N6FVD5|A0A2N6FVD5_9PROT

tr|A0A4R9ABW1|A0A4R9ABW1_9MICO

tr|B8IMC0|B8IMC0_METNO

tr|E1SLH2|E1SLH2_FERBD

tr|A0A2N2HST0|A0A2N2HST0_9DELT

tr|A0A518R1K4|A0A518R1K4_9BURK

tr|A0A1E5MU64|A0A1E5MU64_9ENTR

tr|A0A2T0WMB3|A0A2T0WMB3_9BACT

tr|A0A3A1XDS9|A0A3A1XDS9_GARVA

tr|A0A191UD68|A0A191UD68_9BURK

tr|F6DDE1|F6DDE1_THETG

tr|A0A0L6CTA0|A0A0L6CTA0_9RHOB

tr|D0IL94|D0IL94_9VIBR

tr|A0A520MQI8|A0A520MQI8_9GAMM

tr|A0A4Q7S253|A0A4Q7S253_9RHIZ

tr|A0A2S8Y2I1|A0A2S8Y2I1_9PSED

tr|A0A2R7R8T7|A0A2R7R8T7_9MICC

tr|A0A1I4QK50|A0A1I4QK50_9RHIZ

tr|V0AIE5|V0AIE5_ECOLX

tr|A0A3B9GZZ2|A0A3B9GZZ2_9RHOB

tr|A0A368B9B3|A0A368B9B3_9BACT

tr|A0A0Q4LVS2|A0A0Q4LVS2_9SPHN

tr|D0IE57|D0IE57_9VIBR

tr|M4RJN9|M4RJN9_BIBTR

tr|A0A069SAP2|A0

tr|A0A4V2JJ42|A0A4V2JJ42_STRKA

tr|A0A2U1IH30|A0A2U1IH30_9PSED

tr|A0A196LAP1|A0A196LAP1_9MICO

tr|A0A0R0CRG5|A0A0R0CRG5_9GAMM

tr|A0A0Q9HXW8|A0A0Q9HXW8_9BRAD

tr|A0A3D9MSW4|A0A3D9MSW4_9BURK

tr|B0SLJ7|B0SLJ7_LEPBP

tr|E6KWF4|E6KWF4_9PAST

tr|A0A1G3DIP1|A0A1G3DIP1_9GAMM

tr|A0A1S2TYH3|A0A1S2TYH3_9GAMM

tr|A0A3D9MLQ2|A0A3D9MLQ2_9BURK

tr|A0A2J9E6R0|A0A2J9E6R0_9GAMM

tr|A0A1E4NC37|A0A1E4NC37_9PROT

tr|A0A2H5YEU2|A0A2H5YEU2_9BACT

tr|A0A4U8YYN7|A0A4U8YYN7_METTU

tr|A0A2T5KJS6|A0A2T5KJS6_9PSED

tr|A0A140NHF1|A0A140NHF1_PROSM

tr|M3NF35|M3NF35_HELPX

tr|A0A238J330|A0A238J330_9RHOB

tr|C8T3D7|C8T3D7_KLEPR

tr|A0A3G7ACQ0|A0A3G7ACQ0_9PSED

tr|A0A445ZQK1|A0A445ZQK1_9PSED

tr|A0A445ZSB5|A0A445ZSB5_9PSED

tr|A0A2S9X3S0|A0A2S9X3S0_9NEIS

tr|A0A0Q6XZR6|A0A0Q6XZR6_9PSED

tr|A0A0Q7F879|A0A0Q7F879_9CAUL

tr|A0A3N8BZ98|A0A3N8BZ98_9BURK

tr|J3HAG8|J3HAG8_9GAMM

tr|A0A318I2M2|A0A318I2M2_9FLAO

tr|A0A0P7YK58|A0A0P7YK58_9ALTE

tr|A0A1H3D6T9|A0A1H3D6T9_9PSED

tr|A0A1M3B0Y5|A0A1M3B0Y5_9MICO

tr|A0A2E9D5T8|A0

...

tr|A0A3V1J2B4|A0A3V1J2B4_SALET

tr|A0A3Z7C1D3|A0A3Z7C1D3_SALET

tr|A0A3V0B608|A0A3V0B608_SALET

tr|A0A3V2Y2E2|A0A3V2Y2E2_SALET

tr|A0A3V6WGZ0|A0A3V6WGZ0_SALDE

tr|A0A3V6WCX3|A0A3V6WCX3_SALDE

tr|A0A3U2VU30|A0A3U2VU30_SALET

tr|A0A3U5AUN7|A0A3U5AUN7_SALET

tr|A0A3V3ZE24|A0A3V3ZE24_SALET

tr|A0A3V0TK85|A0A3V0TK85_SALET

tr|A0A3Y0G8R7|A0A3Y0G8R7_SALET

tr|A0A3Z3N6Q2|A0A3Z3N6Q2_SALET

tr|A0A3Z7TNM1|A0A3Z7TNM1_SALET

tr|A0A3Z9W6V2|A0A3Z9W6V2_CAMCO

tr|A0A3Y5DZX6|A0A3Y5DZX6_SALET

tr|A0A486FZV4|A0A486FZV4_KLEPN

tr|A0A3V7ILS4|A0A3V7ILS4_SALRU

tr|A0A3U5ZLN3|A0A3U5ZLN3_ECOLX

tr|A0A4S5SDP7|A0A4S5SDP7_ECOLI

tr|A0A3U7ZSI7|A0A3U7ZSI7_SALET

tr|A0A4S1SJR1|A0A4S1SJR1_ECOLX

tr|A0A5D6L6Y6|A0A5D6L6Y6_KLEPN

tr|A0A3W0TIX7|A0A3W0TIX7_SALET

tr|A0A3V5E330|A0A3V5E330_SALET

tr|A0A4V3QVJ7|A0A4V3QVJ7_ECOLX

tr|A0A3W0TLZ0|A0A3W0TLZ0_SALET

tr|A0A3V9PUF9|A0A3V9PUF9_SALET

tr|A0A3V4SJ64|A0A3V4SJ64_SALET

tr|A0A4S5XGX5|A0A4S5XGX5_ECOLI

tr|A0A5E1QAW6|A0A5E1QAW6_KLEPN

tr|A0A3Y2Q7R2|A0A3Y2Q7R2_SALET

tr|A0A3V

tr|Q133A0|Q133A0_RHOPS

tr|A0A2S9JZL6|A0A2S9JZL6_9RHIZ

tr|A0A2M9EK96|A0A2M9EK96_9GAMM

tr|X6HFB0|X6HFB0_9RHIZ

tr|A0A064EC92|A0A064EC92_CITFR

tr|A0A520WUW3|A0A520WUW3_9SPHN

tr|A0A0B8NWK9|A0A0B8NWK9_9VIBR

tr|A0A1H7NVC0|A0A1H7NVC0_9BRAD

tr|A0A0Q4FPG6|A0A0Q4FPG6_9SPHN

tr|A0A2R7SHD3|A0A2R7SHD3_9PSED

tr|X7EGU4|X7EGU4_9RHOB

tr|A0A4S5CE11|A0A4S5CE11_9GAMM

tr|A0A4U9INH8|A0A4U9INH8_YEREN

tr|B9BZ99|B9BZ99_9BURK

tr|A0A0D6E3P0|A0A0D6E3P0_9GAMM

tr|A0A1L3I8F8|A0A1L3I8F8_9RHOB

tr|A0A396TVY9|A0A396TVY9_9GAMM

tr|A0A351HDR0|A0A351HDR0_9BACT

tr|A0A353G1Z9|A0A353G1Z9_RHISP

tr|A0A0F4IPQ1|A0A0F4IPQ1_9ACTN

tr|A0A0B8P9Y6|A0A0B8P9Y6_9VIBR

tr|F4C9Z1|F4C9Z1_SPHS2

tr|A0A177IER8|A0A177IER8_9CORY

tr|A0A1H2LUI5|A0A1H2LUI5_9PSED

tr|A0A2R7SVM9|A0A2R7SVM9_9PSED

tr|A0A4R8URK5|A0A4R8URK5_9MICO

tr|A0A5B9WMI1|A0A5B9WMI1_9BACT

tr|A0A0J1KUW1|A0A0J1KUW1_9ENTR

tr|A0A0J1NWD0|A0A0J1NWD0_9ENTR

tr|A0A2D4Y2L1|A0A2D4Y2L1_9SPHN

tr|A0A2R9TD59|A0A2R9TD59_YEREN

tr|A0A0U3TXR7|A0A0U3TXR7_BURCE

tr|A0A086WS31|A0

tr|A0A1S2JPI6|A0A1S2JPI6_PSEPU

tr|A0A106XIU1|A0A106XIU1_9BURK

tr|A0A0A2YM11|A0A0A2YM11_9PAST

tr|A0A1B4MXR9|A0A1B4MXR9_9BURK

tr|A0A0M1EKS7|A0A0M1EKS7_STEMA

tr|A0A1L3LL79|A0A1L3LL79_9RHIZ

tr|A0A1Y6GQ60|A0A1Y6GQ60_RAOOR

tr|A0A089PQR7|A0A089PQR7_PLUGE

tr|A0A4U1X6V3|A0A4U1X6V3_9VIBR

tr|I7IX30|I7IX30_9CORY

tr|A0A0T7DP08|A0A0T7DP08_9VIBR

tr|A0A355YU82|A0A355YU82_HALSX

tr|A0A1Y5KT75|A0A1Y5KT75_PSEPU

tr|A0A124YEE6|A0A124YEE6_9BURK

tr|A0A2S9MJ11|A0A2S9MJ11_9BURK

tr|A0A119EKK1|A0A119EKK1_9BURK

tr|A0A506WR72|A0A506WR72_PROMI

tr|A0A1E3EQV5|A0A1E3EQV5_BRAEL

tr|A0A5C5HFB6|A0A5C5HFB6_SALET

tr|A0A1D9LLF8|A0A1D9LLF8_9NEIS

tr|A0A0G9MQW6|A0A0G9MQW6_9SPHN

tr|A2WDT5|A2WDT5_9BURK

tr|A0A3E4IAF6|A0A3E4IAF6_9BACE

tr|A0A1E7YWH8|A0A1E7YWH8_9PROT

tr|A0A2T9HWY7|A0A2T9HWY7_SALET

tr|A0A221DRD3|A0A221DRD3_SERMA

tr|A0A4U1YDY4|A0A4U1YDY4_9VIBR

tr|A0A086ED12|A0A086ED12_9GAMM

tr|A0A2R4HMK5|A0A2R4HMK5_SALEN

tr|A0A344S5A4|A0A344S5A4_SALER

tr|A0A4U2BHB3|A0A4U2BHB3_9VIBR

tr|A0A1H8JAM2|A0A1H8JAM2

tr|A0A285DQL0|A0A285DQL0_9NOCA

tr|A0A419N558|A0A419N558_9GAMM

tr|A0A1L6HS48|A0A1L6HS48_9BURK

tr|A0A2M7NTQ9|A0A2M7NTQ9_9FLAO

tr|A0A2T3VQP2|A0A2T3VQP2_9ACTN

tr|A0A0X3SE69|A0A0X3SE69_9ACTN

tr|I6DQH5|I6DQH5_SHIBO

tr|A0A5C4NFB8|A0A5C4NFB8_9RHOB

tr|C9PN75|C9PN75_9PAST

tr|A0A2A6MAZ7|A0A2A6MAZ7_9RHIZ

tr|A0A257HB35|A0A257HB35_9RHIZ

tr|A0A239HI15|A0A239HI15_9RHOB

tr|Q5FSS8|Q5FSS8_GLUOX

tr|A0A2T6PUG3|A0A2T6PUG3_HELPX

tr|A0A423KA59|A0A423KA59_9PSED

tr|A0A518YGR7|A0A518YGR7_HELPX

tr|A0A3N5D664|A0A3N5D664_HELPX

tr|A0A496FTN8|A0A496FTN8_HELPX

tr|A0A4U8SVM8|A0A4U8SVM8_9HELI

tr|A0A0P1I5Q8|A0A0P1I5Q8_9RHOB

tr|A0A2L0VV00|A0A2L0VV00_9SPHN

tr|A0A348WAE4|A0A348WAE4_9RHOB

tr|A0A423ICM0|A0A423ICM0_9PSED

tr|A0A3S0U876|A0A3S0U876_9MICC

tr|A0A0J6J8G0|A0A0J6J8G0_PSEDM

tr|A0A1G8HE24|A0A1G8HE24_9MICC

tr|T1U8C4|T1U8C4_HELPX

tr|A0A438TGL1|A0A438TGL1_HELPX

tr|A0A438Q680|A0A438Q680_HELPX

tr|A0A543PM49|A0A543PM49_9MICO

tr|A0A3S3B7V9|A0A3S3B7V9_HELPX

tr|A0A1B7HHA8|A0A1B7HHA8_9ENTR

tr|A0A1J

tr|A0A168H9Y6|A0A168H9Y6_MUCCL

tr|A0A507CHI6|A0A507CHI6_9FUNG

tr|A0A397HKI0|A0A397HKI0_9EURO

tr|A0A1L7WEU8|A0A1L7WEU8_9HELO

tr|M1W191|M1W191_CLAP2

tr|O42714|O42714_AGABI

tr|D2IH06|D2IH06_BOTFU

tr|T1QDB8|T1QDB8_ZYMTR

tr|G8EI95|G8EI95_ZYMTR

tr|A0A089WYW9|A0A089WYW9_BOTFU

tr|K5WR01|K5WR01_AGABU

tr|A0A1L7VKJ6|A0A1L7VKJ6_FUSPR

tr|A0A2B7XW13|A0A2B7XW13_9EURO

tr|T1QD25|T1QD25_ZYMTR

tr|G8AE27|G8AE27_9ASCO

tr|A0A2J6TGS5|A0A2J6TGS5_9HELO

tr|A0A364MHA4|A0A364MHA4_ASPFL

tr|A0A397UTK1|A0A397UTK1_9GLOM

tr|C0MN02|C0MN02_HEBCY

tr|G0WEI8|G0WEI8_NAUDC

tr|A0A1R1YNG3|A0A1R1YNG3_9FUNG

tr|A0A2C5ZFV3|A0A2C5ZFV3_9HYPO

tr|A0A1R1X9T4|A0A1R1X9T4_9FUNG

tr|X5D5N9|X5D5N9_ALTAL

tr|A0A0P9EXB3|A0A0P9EXB3_RHOGW

tr|A0A3E2HJN9|A0A3E2HJN9_SCYLI

tr|A0A0E9NA54|A0A0E9NA54_SAICN

tr|A0A4Y7T7B5|A0A4Y7T7B5_9AGAR

tr|T1QD20|T1QD20_ZYMTR

tr|A0A1E3K5W9|A0A1E3K5W9_9TREE

tr|A0A2L2TR69|A0A2L2TR69_9HYPO

tr|G8AE23|G8AE23_MILFA

tr|A7TNK6|A7TNK6_VANPO

tr|A0A367Y1C3|A0A367Y1C3_9ASCO

tr|A0A0C7CN13|A0A0C7CN13

## Create pandas dataframe using seqID & sequences

In [14]:
# create dataframe of 2000 additional isomerase sequences
#d_iso = {'name':seq_ids,'sequence':seqs}
d_1 = {'name':seqID,'sequence':t_seqs}
df = pd.DataFrame(d_1)
df.head()

name  \
0          tr|T0M7Z9|T0M7Z9_CAMFR   
1  tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI   
2  tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO   
3  tr|A0A091CKG8|A0A091CKG8_FUKDA   
4          tr|Q59QN7|Q59QN7_CANAL   

                                            sequence  
0  MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCK...  
1  MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPF...  
2  MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFL...  
3  MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYR...  
4  MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQ...

In [15]:
d_2 = {'name':seq_ids,'sequence':seqs}

df2 = pd.DataFrame(d_2)
df2.head()

name  \
0          tr|T0M7Z9|T0M7Z9_CAMFR   
1  tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI   
2  tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO   
3  tr|A0A091CKG8|A0A091CKG8_FUKDA   
4          tr|Q59QN7|Q59QN7_CANAL   

                                            sequence  
0  MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCK...  
1  MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPF...  
2  MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFL...  
3  MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYR...  
4  MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQ...

In [16]:
df.shape

(39599, 2)

In [17]:
df2.shape

(39599, 2)

In [18]:
# remove non-coding amino acid letters like X,B,U
df['sequence'] = df['sequence'].str.replace('U','G')
df['sequence'] = df['sequence'].str.replace('X','G')
df['sequence'] = df['sequence'].str.replace('B','G')

In [19]:
# remove non-coding amino acid letters like X,B,U
df2['sequence'] = df2['sequence'].str.replace('U','G')
df2['sequence'] = df2['sequence'].str.replace('X','G')
df2['sequence'] = df2['sequence'].str.replace('B','G')

In [20]:
#df['MW'] = df['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df.head()

In [21]:
#df2['MW'] = df2['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df2.head()

In [22]:
# Create 2 columns for the dataframe
df['classification'] = 'IRON-SULFUR-CLUSTER'
df['type'] = 6

df.head(10)

name  \
0          tr|T0M7Z9|T0M7Z9_CAMFR   
1  tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI   
2  tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO   
3  tr|A0A091CKG8|A0A091CKG8_FUKDA   
4          tr|Q59QN7|Q59QN7_CANAL   
5          tr|Q9VWN3|Q9VWN3_DROME   
6          tr|K3YHV8|K3YHV8_SETIT   
7  tr|A0A1Q9C7M6|A0A1Q9C7M6_SYMMI   
8  tr|A0A2E4ASZ9|A0A2E4ASZ9_9PROT   
9          tr|I1I0K5|I1I0K5_BRADI   

                                            sequence       classification  \
0  MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCK...  IRON-SULFUR-CLUSTER   
1  MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPF...  IRON-SULFUR-CLUSTER   
2  MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFL...  IRON-SULFUR-CLUSTER   
3  MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYR...  IRON-SULFUR-CLUSTER   
4  MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQ...  IRON-SULFUR-CLUSTER   
5  MNLLRRQPRLLNKRSTWLFRNYVLANRDVSEPVSRPAAPMSTLSIP...  IRON-SULFUR-CLUSTER   
6  MASVVNEGGRGRRRVGSSSTSKIGIVNQKTKTNGPSPPRAPRPPKK...  IRON-SULFUR-CLUSTER   
7  VRGFQQKAGDIYPDRDAAEHLECVWMQGNAAEQRPHYGPKILHGFF...  IRON-SULFUR-CLUSTER   
8  MAQFTLPTNSKVTSGNHYPAPEGATNTKTFEIYRWSPDDDANPRLD...  IRON-SULFUR-CLUSTER   
9  MAAAALLRRSQTAARALLSPAPLSSRLVASKPHSSSPAPPPPSAST...  IRON-SULFUR-CLUSTER   

   type  
0     6  
1     6  
2     6  
3     6  
4     6  
5     6  
6     6  
7     6  
8     6  
9     6

In [23]:
df.shape

(39599, 4)

In [24]:
# remove the duplicate protein sequences
df = df.drop_duplicates(subset='sequence', keep="first")
df.shape

(31203, 4)

In [25]:
df.head(10)

name  \
0          tr|T0M7Z9|T0M7Z9_CAMFR   
1  tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI   
2  tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO   
3  tr|A0A091CKG8|A0A091CKG8_FUKDA   
4          tr|Q59QN7|Q59QN7_CANAL   
5          tr|Q9VWN3|Q9VWN3_DROME   
6          tr|K3YHV8|K3YHV8_SETIT   
7  tr|A0A1Q9C7M6|A0A1Q9C7M6_SYMMI   
8  tr|A0A2E4ASZ9|A0A2E4ASZ9_9PROT   
9          tr|I1I0K5|I1I0K5_BRADI   

                                            sequence       classification  \
0  MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCK...  IRON-SULFUR-CLUSTER   
1  MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPF...  IRON-SULFUR-CLUSTER   
2  MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFL...  IRON-SULFUR-CLUSTER   
3  MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYR...  IRON-SULFUR-CLUSTER   
4  MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQ...  IRON-SULFUR-CLUSTER   
5  MNLLRRQPRLLNKRSTWLFRNYVLANRDVSEPVSRPAAPMSTLSIP...  IRON-SULFUR-CLUSTER   
6  MASVVNEGGRGRRRVGSSSTSKIGIVNQKTKTNGPSPPRAPRPPKK...  IRON-SULFUR-CLUSTER   
7  VRGFQQKAGDIYPDRDAAEHLECVWMQGNAAEQRPHYGPKILHGFF...  IRON-SULFUR-CLUSTER   
8  MAQFTLPTNSKVTSGNHYPAPEGATNTKTFEIYRWSPDDDANPRLD...  IRON-SULFUR-CLUSTER   
9  MAAAALLRRSQTAARALLSPAPLSSRLVASKPHSSSPAPPPPSAST...  IRON-SULFUR-CLUSTER   

   type  
0     6  
1     6  
2     6  
3     6  
4     6  
5     6  
6     6  
7     6  
8     6  
9     6

## Save dataframe of sequences as a csv file

In [26]:
df.to_csv('uniprot-ironSulfurCluster-Feb1.csv',index = None)

proteins = pd.read_csv('uniprot-ironSulfurCluster-Feb1.csv')

proteins.head()

name  \
0          tr|T0M7Z9|T0M7Z9_CAMFR   
1  tr|A0A1Q9C7M1|A0A1Q9C7M1_SYMMI   
2  tr|A0A2P6TTG2|A0A2P6TTG2_CHLSO   
3  tr|A0A091CKG8|A0A091CKG8_FUKDA   
4          tr|Q59QN7|Q59QN7_CANAL   

                                            sequence       classification  \
0  MAAVVAFSLRRRFPATTLGGACLQQPWLALQDSLARCVKPTGRDCK...  IRON-SULFUR-CLUSTER   
1  MSLAASLRSLAPRGLGRSGLRGFAAMAQPQTFAIYRYDPDQQAKPF...  IRON-SULFUR-CLUSTER   
2  MLSLIRQAGSLGQALCPELTQLVRTVASAAGAAGGASKPVVEKEFL...  IRON-SULFUR-CLUSTER   
3  MAAVAGFSLRRRFPATVLGGSCLQACRGAQTAADRAPRIKKFAIYR...  IRON-SULFUR-CLUSTER   
4  MFRSILHQQKAVQFSVRSLATAAAEKAPRLKKFQIYRWNPDTPEVQ...  IRON-SULFUR-CLUSTER   

   type  
0     6  
1     6  
2     6  
3     6  
4     6

In [27]:
proteins.shape

(31203, 4)